In [1]:
import pandas as pd
from MCForecastTools import MCSimulation
import requests
from dotenv import load_dotenv
import os
import numpy as np
import seaborn as sns
import yfinance as yf
import panel as pn
from panel.interact import interact
from panel import widgets
import plotly.express as px
pn.extension('plotly')

from scipy import optimize
import datetime
import hvplot.pandas
%matplotlib inline

In [2]:
def return_on_lending(amount, interest_rate, duration):
    def xnpv(rate, cashflows):
        return sum([cf/(1+rate)**((t-cashflows[0][0]).days/365.0) for (t,cf) in cashflows])
 
    def xirr(cashflows, guess=0.1):
        try:
            return optimize.newton(lambda r: xnpv(r,cashflows),guess)
        except:
            print('Calc Wrong')

    loan_amount = amount
    rate = interest_rate
    initial_investment = -loan_amount
    monthly_Payment = loan_amount * rate * (30/360)
    last_payment = loan_amount + monthly_Payment
    date_list =['2021-01-06', '2021-01-07', '2021-01-08', '2021-01-09', '2021-01-10', '2021-01-11', '2021-01-12', '2022-01-01', '2022-01-02', '2022-01-03', '2022-01-04', '2022-01-05', '2022-01-06']
    ids_list = [1,2,3,4,5,6,7,8,9,10,11,12,13]
    flows_list = [ initial_investment, monthly_Payment, monthly_Payment, monthly_Payment, monthly_Payment, monthly_Payment, monthly_Payment, monthly_Payment, monthly_Payment, monthly_Payment,  monthly_Payment, monthly_Payment, last_payment]
    df = pd.DataFrame(list(zip(date_list,ids_list,flows_list)), columns=['Date','ID','Flow'])
    df['Date'] = pd.to_datetime(df['Date']).dt.date
    data = list(zip(df['Date'].values,df['Flow'].values))
    value = xirr(data)
    return round((value * amount * duration),2)

In [7]:
# GET TICKERS
tickers = input('What do you want to invest in? (crypto format = ticker-USD, e.g. BTC-USD)').split()

What do you want to invest in? (crypto format = ticker-USD, e.g. BTC-USD) BTC-USD ETH-USD DOGE-USD TSLA AMZN


In [8]:
# GET CAPITAL AMOUNT TO BE INVESTED
capital = int(input('How much do you want to invest?'))

How much do you want to invest? 100000


In [9]:
# GET YEARLY DURATION FOR FORECASTING
duration = int(input('In years, choose a duration for your estimated portfolio returns'))

In years, choose a duration for your estimated portfolio returns 10


In [10]:
# GET HISTORIAL DATA FROM YAHOO FINANCE FOR ASSETS CHOSEN
df_portfolio = yf.download(tickers, start='2015-03-20', end='2020-03-20')

[*********************100%***********************]  5 of 5 completed


In [44]:
# CREATE DATAFRAME OF JUST CLOSING PRICES
df_closing = df_portfolio['Adj Close'].dropna()
df_closing_normalized = df_closing.apply(lambda x: (x - x.min(axis=0)) / (x.max(axis=0) - x.min(axis=0)))
x = pn.widgets.Select(name='Asset', options=[tickers])
df_closing_normalized.hvplot.line(ylabel="Normalized Price", xlabel="Date")

:NdOverlay   [Variable]
   :Curve   [Date]   (value)

In [36]:
df_closing

AMZN      BTC-USD  DOGE-USD     ETH-USD        TSLA
Date                                                                  
2015-08-07   522.619995   279.584991  0.000168    2.772120   48.501999
2015-08-10   524.000000   264.470001  0.000160    0.708448   48.228001
2015-08-11   527.460022   270.385986  0.000164    1.067860   47.473999
2015-08-12   525.909973   266.376007  0.000160    1.217440   47.633999
2015-08-13   529.659973   264.079987  0.000156    1.827670   48.501999
...                 ...          ...       ...         ...         ...
2020-03-13  1785.000000  5563.707031  0.001738  133.201813  109.323997
2020-03-16  1689.150024  5014.479980  0.001587  110.605873   89.014000
2020-03-17  1807.839966  5225.629395  0.001587  113.942749   86.040001
2020-03-18  1830.000000  5238.438477  0.001566  114.842270   72.244003
2020-03-19  1880.930054  6191.192871  0.001773  136.593857   85.528000

[1162 rows x 5 columns]

In [12]:
# CALCULATE DAILY RETURNS
daily_returns = df_closing.pct_change().dropna()

In [13]:
# CALCULATE CORRELATION OF ASSETS 
correlations = daily_returns.corr()

In [14]:
# CALCULATE ANNUALIZED STANDARD DEVIATION OF ASSETS
std_deviations = daily_returns.std()
annualized_std = (std_deviations * np.sqrt(252)).sort_values(ascending=False)

In [15]:
# CALCULATE SHARPE RATIOS
sharpe_ratios = ((daily_returns.mean() * 252)) / (daily_returns.std() * np.sqrt(252))

In [16]:
# CREATE WEIGHTS FOR PORTFOLIOS
low_risk_weights = [.05, .1, .15, .2, .5]
med_risk_weights = [.1, .15, .2, .25, .3]
high_risk_weights = [.3, .25, .2, .15, .1]

# LIST OF ASSETS IN ORDER OF MOST VOLATILE TO LEAST VOLATILE 
volatitly_ranks = annualized_std.index.to_list()

# DAILY RETURNS DATAFRAME REORDERED IN TERMS OF VOLATILITY
ordered_volatility_df_pct = pd.concat([daily_returns[volatitly_ranks[0]], daily_returns[volatitly_ranks[1]],daily_returns[volatitly_ranks[2]],daily_returns[volatitly_ranks[3]],daily_returns[volatitly_ranks[4]]], axis=1, join='inner')

#CLOSING PRICES DATAFRAME REORDERED IN TERMS OF VOLATILITY
ordered_volatility_df_closing = pd.concat([df_closing[volatitly_ranks[0]], df_closing[volatitly_ranks[1]],df_closing[volatitly_ranks[2]],df_closing[volatitly_ranks[3]],df_closing[volatitly_ranks[4]]], axis=1, join='inner')

# RISK APPETITE PORTOLIOS USING DAILY RETURNS DATA
low_risk_portfolio_pct = ordered_volatility_df_pct.dot(low_risk_weights)
med_risk_portfolio_pct = ordered_volatility_df_pct.dot(med_risk_weights)
high_risk_portfolio_pct = ordered_volatility_df_pct.dot(high_risk_weights)

# RISK APPETITE PORTOLIOS USING CLOSE PRICES DATA
low_risk_portfolio_close = ordered_volatility_df_closing.dot(low_risk_weights)
med_risk_portfolio_close = ordered_volatility_df_closing.dot(med_risk_weights)
high_risk_portfolio_close = ordered_volatility_df_closing.dot(high_risk_weights)

In [17]:
# CALCULATE CUMULATIVE RETURNS FOR ALL PORTFOLIOS (DAILY RETURNS DATA)
low_risk_cumulative_returns = (1 + low_risk_portfolio_pct).cumprod() - 1
med_risk_cumulative_returns = (1 + med_risk_portfolio_pct).cumprod() - 1
high_risk_cumulative_returns = (1 + high_risk_portfolio_pct).cumprod() - 1

In [18]:
# CREATE MULTI LEVEL DATAFRAME FOR MONTE CARLO SIMULATIONS
multi_level = pd.concat([ordered_volatility_df_closing], axis=1, keys=['close']).swaplevel(0,1,1)

In [19]:
# CREATE MC INSTANCES OF LOW, MED AND HIGH WEIGHTS

MC_low_risk = MCSimulation(
    portfolio_data = multi_level,
    weights = low_risk_weights,
    num_simulation = 100,
    num_trading_days = 252*duration
)

MC_med_risk = MCSimulation(
    portfolio_data = multi_level,
    weights = med_risk_weights,
    num_simulation = 100,
    num_trading_days = 252*duration
)

MC_high_risk = MCSimulation(
    portfolio_data = multi_level,
    weights = high_risk_weights,
    num_simulation = 100,
    num_trading_days = 252*duration
)

In [20]:
# RUN MONTE CARLO CUMULATIVE RETURN FOR LOW RISK
MC_low_risk.calc_cumulative_return()

Running Monte Carlo simulation number 0.
Running Monte Carlo simulation number 10.
Running Monte Carlo simulation number 20.
Running Monte Carlo simulation number 30.
Running Monte Carlo simulation number 40.
Running Monte Carlo simulation number 50.
Running Monte Carlo simulation number 60.
Running Monte Carlo simulation number 70.
Running Monte Carlo simulation number 80.
Running Monte Carlo simulation number 90.


0           1           2          3           4           5   \
0       1.000000    1.000000    1.000000   1.000000    1.000000    1.000000   
1       0.983152    1.010777    0.988113   0.988684    1.003776    0.989010   
2       0.985574    1.006782    0.982680   0.998576    1.001404    0.993112   
3       0.996657    0.988982    0.998279   0.962942    0.997995    0.998920   
4       1.005473    0.990918    0.981391   0.961190    1.001269    1.007933   
...          ...         ...         ...        ...         ...         ...   
2516  374.275967  895.492972  215.753808  80.977950  143.237512  101.884306   
2517  369.572456  893.942195  212.330658  81.314675  148.800756  101.159802   
2518  378.340097  933.173612  213.193086  80.134803  147.891932   99.256374   
2519  398.084174  907.217960  210.461411  80.562770  150.556502   98.728698   
2520  399.689112  936.064416  204.192548  78.942527  154.951745  101.471664   

              6           7           8           9   ...          90  \
0       1.000000    1.000000    1.000000    1.000000  ...    1.000000   
1       0.999629    1.027161    1.043089    1.020632  ...    0.990036   
2       0.980256    1.012344    1.016286    1.017081  ...    0.977054   
3       1.002921    0.997134    1.014293    0.982027  ...    0.950470   
4       0.997538    0.997416    0.993346    0.994343  ...    0.939406   
...          ...         ...         ...         ...  ...         ...   
2516  121.664851  227.429900  574.671926  102.036105  ...  366.591074   
2517  123.972600  229.881524  562.616252  104.112228  ...  365.834930   
2518  120.725695  231.894752  558.922921  103.540017  ...  363.301794   
2519  124.663112  228.145969  558.744534  102.919954  ...  358.610545   
2520  121.023729  232.110017  560.540223  102.031676  ...  361.568219   

              91          92           93          94          95         96  \
0       1.000000    1.000000     1.000000    1.000000    1.000000   1.000000   
1       0.999638    1.010381     1.045290    1.002588    1.012588   1.006068   
2       0.971105    1.024079     1.061295    0.995028    1.015067   1.015713   
3       0.993627    1.061891     1.053587    0.985243    1.036449   0.995398   
4       1.026789    1.081144     1.079594    0.983538    1.024549   0.958403   
...          ...         ...          ...         ...         ...        ...   
2516  207.587508  448.356261  1706.757554  299.831867  422.549384  72.492441   
2517  208.750035  443.554113  1716.725925  306.204768  415.198900  72.507691   
2518  209.174272  436.603437  1739.728260  306.410612  408.736371  73.547834   
2519  215.902731  436.919761  1771.025899  305.129060  413.180243  72.790217   
2520  217.532036  433.054271  1769.257250  313.621323  412.539115  71.765874   

               97          98          99  
0        1.000000    1.000000    1.000000  
1        1.016248    1.019159    1.004049  
2        0.994874    0.997642    1.046375  
3        1.003966    0.981364    1.026461  
4        1.008051    1.002401    1.028721  
...           ...         ...         ...  
2516  1684.710810  147.209856  159.111909  
2517  1675.071384  149.944248  163.102323  
2518  1700.517018  148.275680  162.851960  
2519  1713.022305  150.090005  159.514516  
2520  1756.753510  150.191660  157.793983  

[2521 rows x 100 columns]

In [21]:
# RUN MONTE CARLO CUMULATIVE RETURN FOR MEDIUM RISK
MC_med_risk.calc_cumulative_return()

Running Monte Carlo simulation number 0.
Running Monte Carlo simulation number 10.
Running Monte Carlo simulation number 20.
Running Monte Carlo simulation number 30.
Running Monte Carlo simulation number 40.
Running Monte Carlo simulation number 50.
Running Monte Carlo simulation number 60.
Running Monte Carlo simulation number 70.
Running Monte Carlo simulation number 80.
Running Monte Carlo simulation number 90.


0           1            2           3            4   \
0        1.000000    1.000000     1.000000    1.000000     1.000000   
1        1.011758    1.030385     1.034511    0.989889     1.035488   
2        1.078540    1.024887     1.015548    1.001720     1.021291   
3        1.087499    1.049096     1.003784    1.004789     1.050229   
4        1.119583    1.013144     1.017082    1.016715     1.064037   
...           ...         ...          ...         ...          ...   
2516  2181.034519  283.377282  3283.453511  336.115414  3397.492985   
2517  2198.484007  283.520223  3351.425237  335.867189  3436.066874   
2518  2160.186872  287.421419  3284.208667  340.920115  3371.335736   
2519  2191.476579  292.204756  3355.750541  347.825122  3419.913923   
2520  2220.138107  300.890601  3270.376958  358.501654  3407.108182   

               5            6            7           8           9   ...  \
0        1.000000     1.000000     1.000000    1.000000    1.000000  ...   
1        0.997736     0.990192     1.011616    0.987932    1.008527  ...   
2        0.979990     1.017316     1.014051    1.011849    1.014292  ...   
3        0.957550     0.981800     1.014359    0.983820    1.051102  ...   
4        0.965845     0.960663     1.016399    0.970852    1.043278  ...   
...           ...          ...          ...         ...         ...  ...   
2516  1644.951129  1871.052904  2009.595366  759.086879  147.880634  ...   
2517  1647.904748  1918.646087  1942.456205  754.614412  145.215403  ...   
2518  1668.425547  1934.254037  1989.418383  781.441248  147.179792  ...   
2519  1730.714490  1906.634014  2045.181191  762.890485  147.354029  ...   
2520  1757.809654  1874.474605  2030.822675  753.619235  146.140722  ...   

              90           91          92           93           94  \
0       1.000000     1.000000    1.000000     1.000000     1.000000   
1       1.022409     1.022022    1.013494     1.021120     0.982339   
2       1.006081     1.030672    1.030797     0.965184     0.980869   
3       0.974988     1.045578    1.049357     0.956967     0.987294   
4       0.993050     1.030458    1.046058     0.946704     0.976542   
...          ...          ...         ...          ...          ...   
2516  290.511013  2067.107417  709.950197  4612.516932   998.074278   
2517  299.451138  2046.007494  701.281815  4566.786125   981.338802   
2518  292.848248  2053.595652  715.222741  4518.505764   986.236940   
2519  290.653168  2044.268874  721.168696  4629.663637  1021.328132   
2520  287.373449  2044.875259  720.570923  4667.043765  1021.678628   

              95           96          97          98           99  
0       1.000000     1.000000    1.000000    1.000000     1.000000  
1       0.999740     1.027847    1.004014    1.011852     0.996219  
2       0.990452     1.016251    0.983461    1.043949     0.981458  
3       0.966135     1.020431    0.957772    1.034432     1.011061  
4       0.962123     1.020400    0.964497    1.056673     1.031636  
...          ...          ...         ...         ...          ...  
2516  622.332513  2667.985887  783.909994  745.188112  1000.470249  
2517  629.363219  2557.530194  773.923060  755.839715   990.806112  
2518  638.811483  2508.842899  781.253532  755.220177   961.307822  
2519  639.843356  2507.209879  777.339696  760.588191   943.344407  
2520  627.221696  2482.580843  766.331575  775.593318   946.024903  

[2521 rows x 100 columns]

In [22]:
# RUN MONTE CARLO CUMULATIVE RETURN FOR HIGH RISK
MC_high_risk.calc_cumulative_return()

Running Monte Carlo simulation number 0.
Running Monte Carlo simulation number 10.
Running Monte Carlo simulation number 20.
Running Monte Carlo simulation number 30.
Running Monte Carlo simulation number 40.
Running Monte Carlo simulation number 50.
Running Monte Carlo simulation number 60.
Running Monte Carlo simulation number 70.
Running Monte Carlo simulation number 80.
Running Monte Carlo simulation number 90.


0             1             2            3             4   \
0       1.000000      1.000000      1.000000     1.000000      1.000000   
1       1.007182      1.005966      0.991056     1.008862      1.023483   
2       0.975894      1.036753      0.980277     0.963158      1.041961   
3       1.012476      1.050131      0.987233     0.995877      1.029483   
4       1.003377      1.064796      1.037093     0.999338      1.062371   
...          ...           ...           ...          ...           ...   
2516  387.887293  18155.849563   8588.082903  1098.597508  29945.549972   
2517  401.134779  19523.632257   9082.781279  1131.860783  29176.669728   
2518  387.123349  18282.628281  10005.215917  1188.541936  27846.613612   
2519  384.519502  18227.623686  10156.234865  1248.877116  27257.648584   
2520  388.985239  20145.409179  10528.724805  1212.637937  25948.673925   

             5           6              7            8            9   ...  \
0      1.000000    1.000000       1.000000     1.000000     1.000000  ...   
1      0.951749    1.043809       0.953582     1.039048     1.048856  ...   
2      0.920553    1.026921       0.963486     1.038562     1.076208  ...   
3      0.936870    0.974917       0.948760     1.107623     1.093948  ...   
4      0.978139    0.950949       0.957225     1.104308     1.011180  ...   
...         ...         ...            ...          ...          ...  ...   
2516  27.668977  687.450706  302228.374379  5532.667101  4144.097715  ...   
2517  28.975486  708.222369  303951.469124  5632.387652  4255.047993  ...   
2518  29.844678  647.144231  306978.208941  5550.400810  4278.417580  ...   
2519  29.888108  657.500561  319733.529790  5619.289162  4454.280362  ...   
2520  30.927954  649.295697  328873.209253  6006.584597  4461.435913  ...   

                90            91            92            93           94  \
0     1.000000e+00      1.000000      1.000000      1.000000     1.000000   
1     9.778705e-01      0.945979      0.982692      1.021549     0.997757   
2     1.037216e+00      0.968518      0.996707      1.020021     0.943239   
3     1.088961e+00      0.942086      0.946108      1.073253     0.871049   
4     1.132894e+00      0.923635      1.015805      1.121072     0.838614   
...            ...           ...           ...           ...          ...   
2516  1.743799e+06  11407.071014  72270.895081  26716.993494  3948.727052   
2517  1.698873e+06  11062.941564  70103.173257  27430.369007  4272.564679   
2518  1.708959e+06  11119.294794  70913.623979  26333.995117  4533.497510   
2519  1.747784e+06  11460.117203  69012.397005  25063.553815  4467.262231   
2520  1.766488e+06  11276.944533  71901.848370  23735.928076  4595.348977   

                95            96            97            98           99  
0         1.000000      1.000000      1.000000      1.000000     1.000000  
1         1.035011      0.984998      0.983554      1.015135     0.995470  
2         0.983048      0.966554      0.997276      0.981904     0.996210  
3         1.036004      0.981940      0.991618      0.903666     1.030619  
4         1.052443      1.002496      0.980376      0.886796     1.048109  
...            ...           ...           ...           ...          ...  
2516  13040.760008  54279.086518   9589.981449  43258.940653  7840.468182  
2517  12907.004993  54650.928685   9705.658757  45774.968968  8086.153550  
2518  12334.913911  53253.395895  10026.741227  46272.520033  8422.269174  
2519  12131.106100  51997.333941   9859.324022  43792.624656  8161.589085  
2520  11889.063864  53663.242635   9773.165349  42299.871126  8202.182295  

[2521 rows x 100 columns]

In [23]:
# CREATE SUMMARY STATS FOR EACH MONTE CARLO SIMULATION
low_risk_table = MC_low_risk.summarize_cumulative_return()
med_risk_table = MC_med_risk.summarize_cumulative_return()
high_risk_table = MC_high_risk.summarize_cumulative_return()

In [47]:
# RISK/ASSET ANALYSIS VISUALIZATIONS
from bokeh.models import NumeralTickFormatter

daily_returns_hist = daily_returns.hvplot.hist(ylabel="Frequency", xlabel="Percent Change",bins=100, figsize=(25,10))
#closing_prices_line = df_closing.hvplot.line(ylabel="Price", xlabel="Date", logy=True)
x = pn.widgets.Select(name='Asset', options=[tickers])
closing_prices_line = df_closing_normalized.hvplot.line(ylabel="Normalized Price", xlabel="Date").opts(yformatter=NumeralTickFormatter(format="$0,000.00"))
correlations_heatmap = correlations.hvplot.heatmap(cmap=["#75968f", "#a5bab7", "#c9d9d3", "#e2e2e2", "#dfccce", "#ddb7b1", "#cc7878", "#933b41", "#550b1d"])
std_devs_bar = annualized_std.hvplot.bar(ylabel="Standard Deviation")
sharpe_ratios_bar = sharpe_ratios.hvplot.bar(ylabel="Sharpe Ratio")

# PORTFOLIO PERFORMANCE VISUALIZATIONS
low_risk_close_plot = low_risk_portfolio_close.hvplot.line(ylabel="Dollar Return",label="Low Risk").opts(show_legend=True)
med_risk_close_plot = med_risk_portfolio_close.hvplot.line(label="Medium Risk").opts(show_legend=True)
high_risk_close_plot = high_risk_portfolio_close.hvplot.line(label="High Risk").opts(show_legend=True)
portfolios_plot_close_data = (low_risk_close_plot * med_risk_close_plot * high_risk_close_plot).opts(ylabel="Dollar Return",
    legend_position="top_left",yformatter=NumeralTickFormatter(format="$0,000.00"),shared_axes=False)

low_risk_cumulative_plot = low_risk_cumulative_returns.hvplot(ylabel="Percentage Return",label="Low Risk").opts(show_legend=True)
med_risk_cumulative_plot = med_risk_cumulative_returns.hvplot(label="Medium Risk").opts(show_legend=True)
high_risk_cumulative_plot = high_risk_cumulative_returns.hvplot(label="High Risk").opts(show_legend=True)
portfolios_plot_cumulative_data = (low_risk_cumulative_plot * med_risk_cumulative_plot * high_risk_cumulative_plot).opts(legend_position="top_left",shared_axes=False)

# MONTE CARLO VISUALIZATIONS
low_returns_data = {
    "mean": list(MC_low_risk.simulated_return.mean(axis=1)),
    "median":list(MC_low_risk.simulated_return.median(axis=1)),
    "max":list(MC_low_risk.simulated_return.max(axis=1)),
    "min":list(MC_low_risk.simulated_return.min(axis=1))
}
low_return_df = pd.DataFrame(low_returns_data)
low_risk_MC_plot = low_return_df.hvplot(ylabel="Simulated Cumulative Returns",xlabel="Number of Trading Days")

medium_returns_data = {
    "mean": list(MC_med_risk.simulated_return.mean(axis=1)),
    "median":list(MC_med_risk.simulated_return.median(axis=1)),
    "max":list(MC_med_risk.simulated_return.max(axis=1)),
    "min":list(MC_med_risk.simulated_return.min(axis=1))
}
medium_return_df = pd.DataFrame(medium_returns_data)
med_risk_MC_plot = medium_return_df.hvplot(ylabel="Simulated Cumulative Returns",xlabel="Number of Trading Days")

high_returns_data = {
    "mean": list(MC_high_risk.simulated_return.mean(axis=1)),
    "median":list(MC_high_risk.simulated_return.median(axis=1)),
    "max":list(MC_high_risk.simulated_return.max(axis=1)),
    "min":list(MC_high_risk.simulated_return.min(axis=1))
}
high_return_df = pd.DataFrame(high_returns_data)
high_risk_MC_plot = high_return_df.hvplot(ylabel="Simulated Cumulative Returns",xlabel="Number of Trading Days")



In [48]:
def lendingViz():
    return interact(return_on_lending, amount=(capital*.2,capital*.5), interest_rate=(0.01,0.07,0.001), duration=duration)

In [49]:
# DASHBOARD CREATION

daily_returns_col = pn.Column('## Daily Returns', daily_returns_hist)
sharpe_ratios_col = pn.Column('## Sharpe Ratios', sharpe_ratios_bar)
daily_closing_col = pn.Column('## Closing Prices', closing_prices_line)
std_dev_col = pn.Column('## Annualized STDs', std_devs_bar)
correlations_col = pn.Column('## Correlations', correlations_heatmap)
low_risk_mc_col = pn.Column('## Monte Carlo Low Risk Portfolio', low_risk_MC_plot)
med_risk_mc_col = pn.Column('## Monte Carlo Medium Risk Portfolio', med_risk_MC_plot)
high_risk_mc_col = pn.Column('## Monte Carlo High Risk Portfolio', high_risk_MC_plot)

portfolio_close_col = pn.Column('## Portfolio Close Data', portfolios_plot_close_data)
portfolio_cumulative_col = pn.Column('## Portfolio Cumulative Returns', portfolios_plot_cumulative_data)

risk_analysis_tabs = pn.Tabs(
    ('Closing Prices', daily_closing_col),
    ('Daily Returns', daily_returns_col),
    ('Sharpe Ratios', sharpe_ratios_col),
    ('Standard Deviations', std_dev_col),
    ('Correlations', correlations_col)
)

lending_tab = pn.Tabs(
    ('Lending Interaction', lendingViz())
)

portfolio_performace_tab = pn.Tabs(
    ('Dollar Returns', portfolio_close_col),
    ('Percentage Returns', portfolio_cumulative_col)
)

mc_tab = pn.Tabs(
    ('Low', low_risk_mc_col),
    ('Medium', med_risk_mc_col),
    ('High', high_risk_mc_col)
)
mainTabs = pn.Tabs(
    ('Risk Analysis', risk_analysis_tabs),
    ('Performance', portfolio_performace_tab),
    ('Monte Carlo', mc_tab),
    ('Lending', lending_tab)
)
dashboard = pn.Column('# Analysis', mainTabs)

In [50]:
dashboard

Column
    [0] Markdown(str)
    [1] Tabs
        [0] Tabs
            [0] Column
                [0] Markdown(str)
                [1] HoloViews(NdOverlay)
            [1] Column
                [0] Markdown(str)
                [1] HoloViews(NdOverlay)
            [2] Column
                [0] Markdown(str)
                [1] HoloViews(Bars)
            [3] Column
                [0] Markdown(str)
                [1] HoloViews(Bars)
            [4] Column
                [0] Markdown(str)
                [1] HoloViews(HeatMap)
        [1] Tabs
            [0] Column
                [0] Markdown(str)
                [1] HoloViews(Overlay)
            [1] Column
                [0] Markdown(str)
                [1] HoloViews(Overlay)
        [2] Tabs
            [0] Column
                [0] Markdown(str)
                [1] HoloViews(NdOverlay)
            [1] Column
                [0] Markdown(str)
                [1] HoloViews(NdOverlay)
            [2] Column
                [0] Markdown(str)
                [1] HoloViews(NdOverlay)
        [3] Tabs
            [0] Column
                [0] Column
                    [0] FloatSlider(end=50000.0, name='amount', start=20000.0, value=35000.0)
                    [1] FloatSlider(end=0.07, name='interest_rate', start=0.01, step=0.001, value=0.04)
                    [2] IntSlider(end=30, name='duration', start=-10, value=10)
                [1] Row
                    [0] Str(float64, name='interactive10888')

In [ ]:
 # Use the lower and upper `95%` confidence intervals to calculate the range of the possible outcomes of our $15,000 investments in stocks
def mc_and_lending_summary(capital, duration):
    
    low_risk_investment_amount = capital * .8
    low_risk_lending_amount = capital * .2
    
    med_risk_investment_amount = capital * .6
    med_risk_lending_amount = capital * .4
    
    high_risk_investment_amount = capital * .5
    high_risk_lending_amount = capital * .5
    
    low_risk_ci_lower = round(low_risk_table[8]*low_risk_investment_amount,2)
    low_risk_ci_upper = round(low_risk_table[9]*low_risk_investment_amount,2)
    med_risk_ci_lower = round(med_risk_table[8]*med_risk_investment_amount,2)
    med_risk_ci_upper = round(med_risk_table[9]*med_risk_investment_amount,2)
    high_risk_ci_lower = round(high_risk_table[8]*high_risk_investment_amount,2)
    high_risk_ci_upper = round(high_risk_table[9]*high_risk_investment_amount,2)
    
    low_risk_lending_profit = return_on_lending(low_risk_lending_amount, .075, duration)
    med_risk_lending_profit = return_on_lending(med_risk_lending_amount, .1, duration)
    high_risk_lending_profit = return_on_lending(high_risk_lending_amount, .14, duration)
    # Print results
    print("--------\033[1m\033[92m\033[4mUsing Your Investment Capital 0f "+ "${:,.2f}".format(capital)+"\033[0m---------")
    print("----------------------------------------------------------")
    print("----------------------------------------------------------")
    print('\033[1m'+'\033[94m'+"FOR LOW RISK INVESTMENT\033[0m \033[94m(80% in your portfolio and 20% in lending)"+'\033[0m')
    print(
        "\033[1m"+"${:,.2f}".format(low_risk_investment_amount)+"\033[0m will be invested in the low risk portfolio and\n"
        "\033[1m"+"${:,.2f}".format(low_risk_lending_amount)+"\033[0m will be invested in lending.\n"
        f"Over the next \033[1m{duration}\033[0m year(s), there is a 95% chance that the low risk porfolio will end within the range of"
        " \033[1m"+"${:,.2f}".format(low_risk_ci_lower)+"\033[0m and \033[1m"+"${:,.2f}".format(low_risk_ci_upper)+"\033[0m.\n"
        "And lending would yield \033[1m"+"${:,.2f}".format(low_risk_lending_profit)+"\033[0m in profit."
    )
    print("----------------------------------------------------------")
    print('\033[1m'+'\033[91m'+"FOR MEDIUM RISK INVESTMENT\033[0m \033[91m(60% in your portfolio and 40% in lending)"+'\033[0m')
    print(
        "\033[1m"+"${:,.2f}".format(med_risk_investment_amount)+"\033[0m will be invested in the medium risk portfolio and\n"
        "\033[1m"+"${:,.2f}".format(med_risk_lending_amount)+"\033[0m will be invested in lending.\n"
        f"Over the next \033[1m{duration}\033[0m year(s), there is a 95% chance that the medium risk porfolio will end within the range of"
        " \033[1m"+"${:,.2f}".format(med_risk_ci_lower)+"\033[0m and \033[1m"+"${:,.2f}".format(med_risk_ci_upper)+"\033[0m.\n"
        "And lending would yield \033[1m"+"${:,.2f}".format(med_risk_lending_profit)+"\033[0m in profit."
         )
    print("----------------------------------------------------------")
    print('\033[1m'+'\033[93m'+"FOR HIGH RISK INVESTMENT\033[0m \033[93m(50% in your portfolio and 50% in lending)"+'\033[0m')
    print(
        "\033[1m"+"${:,.2f}".format(high_risk_investment_amount)+"\033[0m will be invested in the high risk portfolio and\n"
        "\033[1m"+"${:,.2f}".format(high_risk_lending_amount)+"\033[0m will be invested in lending.\n"
        f"Over the next \033[1m{duration}\033[0m year(s), there is a 95% chance that the high risk porfolio will end within the range of"
        " \033[1m"+"${:,.2f}".format(high_risk_ci_lower)+"\033[0m and \033[1m"+"${:,.2f}".format(high_risk_ci_upper)+"\033[0m.\n"
        "And lending would yield \033[1m"+"${:,.2f}".format(high_risk_lending_profit)+"\033[0m in profit."
         ) 

In [ ]:
mc_and_lending_summary(capital, duration)